In [1]:
!pip install simpletransformers

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.4/42.4 kB 1.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.6/43.6 kB 2.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 316.3/316.3 kB 12.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.4/9.4 MB 67.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 527.3/527.3 kB 30.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.7/8.7 MB 76.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.7/101.7 kB 8.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 8.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.3/207.3 kB 18.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 39.9/39.9 MB 21.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.9/6.9 MB 89.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 309.1/309.1 kB 22.2 MB/s eta 0:00:00
   ━━

In [2]:
!unzip archive.zip

Archive:  archive.zip
  inflating: metadata                
  inflating: test.txt                
  inflating: train.txt               
  inflating: valid.txt               


In [3]:
import os
train_file_path = '/content/train.txt'
valid_file_path = '/content/valid.txt'

# Reading the files
with open(train_file_path, 'r') as file:
    train_lines = file.readlines()

with open(valid_file_path, 'r') as file:
    valid_lines = file.readlines()

# Display the first few lines of each to understand the structure
train_lines[:10], valid_lines[:10]

(['-DOCSTART- -X- -X- O\n',
  '\n',
  'EU NNP B-NP B-ORG\n',
  'rejects VBZ B-VP O\n',
  'German JJ B-NP B-MISC\n',
  'call NN I-NP O\n',
  'to TO B-VP O\n',
  'boycott VB I-VP O\n',
  'British JJ B-NP B-MISC\n',
  'lamb NN I-NP O\n'],
 ['-DOCSTART- -X- -X- O\n',
  '\n',
  'CRICKET NNP B-NP O\n',
  '- : O O\n',
  'LEICESTERSHIRE NNP B-NP B-ORG\n',
  'TAKE NNP I-NP O\n',
  'OVER IN B-PP O\n',
  'AT NNP B-NP O\n',
  'TOP NNP I-NP O\n',
  'AFTER NNP I-NP O\n'])

In [4]:
import pandas as pd
def process_dataset(lines):
    sentence_id = 0
    data = []

    for line in lines:
        if line.strip() == "":  # New sentence starts after a blank line
            sentence_id += 1
        elif not line.startswith('-DOCSTART-'):
            parts = line.split()
            word = parts[0]
            label = parts[-1]  # The last part is the label
            data.append([sentence_id, word, label])

    return pd.DataFrame(data, columns=["sentence_id", "words", "labels"])

train_data=process_dataset(train_lines)
eval_data=process_dataset(valid_lines)

train_data.head(10), eval_data.head(10)


(   sentence_id    words  labels
 0            1       EU   B-ORG
 1            1  rejects       O
 2            1   German  B-MISC
 3            1     call       O
 4            1       to       O
 5            1  boycott       O
 6            1  British  B-MISC
 7            1     lamb       O
 8            1        .       O
 9            2    Peter   B-PER,
    sentence_id           words labels
 0            1         CRICKET      O
 1            1               -      O
 2            1  LEICESTERSHIRE  B-ORG
 3            1            TAKE      O
 4            1            OVER      O
 5            1              AT      O
 6            1             TOP      O
 7            1           AFTER      O
 8            1         INNINGS      O
 9            1         VICTORY      O)

In [6]:
# Saving the Dataset for Further Use

train_data.to_csv('train_data.csv', index=False)
eval_data.to_csv('eval_data.csv', index=False)

In [7]:
from simpletransformers.ner import NERModel,NERArgs

model_args=NERArgs(train_batch_size=8,evaluate_during_training=True, num_train_epochs=1, output_dir='./finetuned')
model=NERModel('roberta', 'roberta-base', args=model_args, use_cuda=True)


# Train the model
model.train_model(train_data, eval_data=eval_data)

config.json:   0%|          | 0.00/481 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/499M [00:00<?, ?B/s]

Some weights of RobertaForTokenClassification were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


tokenizer_config.json:   0%|          | 0.00/25.0 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/899k [00:00<?, ?B/s]

...

/usr/local/lib/python3.10/dist-packages/simpletransformers/ner/ner_model.py:782: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast():
/usr/local/lib/python3.10/dist-packages/torch/optim/lr_scheduler.py:216: UserWarning: Detected call of `lr_scheduler.step()` before `optimizer.step()`. In PyTorch 1.1.0 and later, you should call them in the opposite order: `optimizer.step()` before `lr_scheduler.step()`.  Failure to do this will result in PyTorch skipping the first value of the learning rate schedule. See more details at https://pytorch.org/docs/stable/optim.html#how-to-adjust-learning-rate
  warnings.warn(


  0%|          | 0/2 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/33 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/ner/ner_model.py:1303: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast():


(1756,
 defaultdict(list,
             {'global_step': [1756],
              'train_loss': [0.002414226531982422],
              'eval_loss': [0.04242714098125527],
              'precision': [0.9331215515800033],
              'recall': [0.9408293998651382],
              'f1_score': [0.9369596239402334]}))

In [8]:
# Evaluate the model
result, model_outputs, preds_list = model.eval_model(eval_data)

print(model_outputs)
print(preds_list)

/usr/lib/python3.10/multiprocessing/popen_fork.py:66: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  self.pid = os.fork()


  0%|          | 0/2 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/33 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/simpletransformers/ner/ner_model.py:1303: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast():


[[[[8.11, -0.02325, -0.477, -0.2522, -2.752, -0.242, -1.062, -1.256, -2.346], [8.36, -0.364, -0.0917, -0.7275, -2.537, -0.6865, -0.8286, -1.418, -2.111], [8.21, -0.2456, -0.0414, -0.606, -2.756, -0.729, -0.913, -1.317, -2.04]], [[9.414, -1.037, -0.5586, -0.8687, -2.46, -0.94, -0.516, -1.715, -1.777]], [[1.701, 1.346, -2.424, 3.5, -2.705, 3.227, -2.75, 1.117, -3.463], [1.644, -0.634, 0.5376, -0.3933, -0.3728, -1.052, 2.514, -2.248, -0.842], [3.676, -1.884, 0.9, -0.8047, -0.2827, -1.269, 1.923, -2.404, -0.749], [4.37, -2.021, 0.3555, -0.9004, -0.84, -0.953, 2.014, -2.23, -1.05], [8.81, -1.638, -0.1688, -1.427, -2.049, -1.314, 0.332, -2.275, -1.644], [9.32, -1.081, -0.748, -0.9854, -2.383, -0.655, -0.4456, -1.52, -1.98]], [[9.41, -1.031, -0.7246, -0.8813, -2.453, -0.6816, -0.639, -1.601, -2.023], [8.84, -0.4907, -0.4255, -0.798, -2.51, -0.5435, -0.6216, -1.28, -1.934]], [[8.664, -0.74, 0.1407, -1.042, -2.357, -0.9126, -0.7095, -1.889, -1.806]], [[9.016, -0.5835, -0.2847, -0.9404, -2.574, 

In [11]:
# Make predictions with the model

model = NERModel("roberta", "finetuned", use_cuda=True)

predictions, raw_outputs = model.predict(["Hermione was the best in her class"])

print(predictions)

print(raw_outputs)

/usr/lib/python3.10/multiprocessing/popen_fork.py:66: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  self.pid = os.fork()


  0%|          | 0/1 [00:00<?, ?it/s]

Running Prediction:   0%|          | 0/1 [00:00<?, ?it/s]

[[{'Hermione': 'B-PER'}, {'was': 'O'}, {'the': 'O'}, {'best': 'O'}, {'in': 'O'}, {'her': 'O'}, {'class': 'O'}]]
[[{'Hermione': [[-0.8438, -0.2778, -2.215, 7.0, -1.316, 1.357, -2.639, 0.561, -2.795], [-1.382, -1.707, -0.3623, 0.419, 6.22, -2.002, 0.259, -2.205, -0.5513]]}, {'was': [[9.92, -2.03, -0.868, -1.226, -1.808, -1.52, -0.468, -2.197, -1.493]]}, {'the': [[10.05, -1.822, -0.9937, -1.148, -2.07, -1.185, -0.631, -2.07, -1.63]]}, {'best': [[10.086, -1.548, -0.967, -1.129, -2.24, -1.048, -0.819, -1.967, -1.799]]}, {'in': [[9.984, -1.863, -0.8174, -1.333, -2.074, -1.339, -0.4436, -2.186, -1.478]]}, {'her': [[9.88, -1.644, -1.02, -1.261, -2.182, -1.124, -0.7793, -2.117, -1.773]]}, {'class': [[9.55, -1.392, -0.6143, -1.338, -2.258, -1.425, -0.784, -2.076, -1.879]]}]]


/usr/local/lib/python3.10/dist-packages/simpletransformers/ner/ner_model.py:1643: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast():
